In [1]:
import matplotlib.pyplot as plt
import numpy as np
import yfinance as yf
import pandas as pd
from datetime import datetime
from datetime import date
from datetime import timedelta
from matplotlib.animation import FFMpegWriter
from matplotlib import cm
import matplotlib.animation as anim

In [2]:
# Purchases a stock
def addStock(stock_name, total_amount_invested, purchase_price, sell_price, allocation, time_invested_for, frequency):
    stock = yf.Ticker(stock_name)
    amount_invested = total_amount_invested * allocation
    hist = stock.history(period=time_invested_for)
    hist_arr = np.array(hist)
    num_shares = amount_invested / hist_arr[0][purchase_price]
    ending_balance = num_shares * hist_arr[len(hist_arr)-1][sell_price]
    return amount_invested, ending_balance, hist_arr

In [3]:
# Generates growth of stocks for all stocks in portfolio
def portfolioGenerator(stocks, amount_invested, purchase_price, sell_price, duration, frequency, decimal_places):
    starting_investments = []
    ending_investments = []
    stock_data = []

    for stock in stocks:
        start, end, data = addStock(stock[0], amount_invested, purchase_price, sell_price, stock[1], duration, frequency)
        starting_investments.append(start)
        ending_investments.append(end)
        stock_data.append(data)
        period_yield = end / start - 1
        print(stock[0], " Starting: $", round(start, decimal_places), " Ending: $", round(end, decimal_places), " ", duration, " Yield: ", round(period_yield * 100, decimal_places), "%")

    print("\nStarting Portfolio Amount: $", round(sum(starting_investments), decimal_places), " Ending Portfolio Amount: $", round(sum(ending_investments), decimal_places), " Overall Yield: ", round(100 * (sum(ending_investments) / sum(starting_investments) - 1), decimal_places), "%")
    return stock_data

In [4]:
# Finds the starting date based on time invested
def modifyDate(end_date, time_invested_for, len_data):
    ind_to_modify = 0
    modify_amount = 1
    today = date.today()
    if ("ytd" in time_invested_for):
        return date(int(end_date.year), 1, 1)
    elif ("d" in time_invested_for):
        delta = timedelta(days=(1+int(time_invested_for[0])))
        return end_date-delta
    elif ("mo" in time_invested_for):
        delta = timedelta(days=(1+30*int(time_invested_for[0])))
        return end_date-delta
    elif ("y" in time_invested_for):
        if (len(time_invested_for) == 2):
            delta = timedelta(days=1, weeks=(52*int(time_invested_for[0])))
            return end_date-delta
        else:
            delta = timedelta(days=1, weeks=(52*int(time_invested_for[0:2])))
            return end_date-delta
    else:
        dates = pd.bdate_range(end = today, periods = len_data).tolist()
        return dates[0]

In [5]:
# Calculates the percentage yield of the end price relative to the start price, rounded to decimal_places
def findYield(start_price, end_price, decimal_places):
    return round(100 * (end_price / start_price - 1), decimal_places)

In [6]:
# Plots growth of stocks
def plotStockGrowth(stocks, stock_data, duration):
    plt.figure(figsize=(15,5))
    plt.title("Stock Growth - " + duration)
    plt.xlabel("Date")
    plt.ylabel("Value in USD")
    today = date.today()
    #today = today.strftime("%Y/%m/%d")
    start_date = modifyDate(today, duration, len(stocks[0]))
    dates = pd.bdate_range(start=start_date,end=today)
    stock_names = []
    
    for stock in stocks:
        stock_names.append(stock)
        
    for s in range(0, len(stocks)):
        nums = []
        for val in stock_data[s]:
            nums.append(val[0])
        plt.plot(dates[0:len(nums)], nums, label=stock_names[s][0])
        
    plt.legend()
    plt.show()

In [15]:
# Animates growth of stocks
%matplotlib osx
def animateStockGrowth(stocks, stock_data, duration):
    plt.figure(figsize=(15,5))
    plt.title("Stock Growth - " + duration)
    plt.xlabel("Date")
    plt.ylabel("Value in USD")
    today = datetime.today()
    start_date = modifyDate(today, duration, len(stocks[0]))
    dates = pd.bdate_range(start=start_date,end=today)
    stock_names = []
    
    metadata = dict(title='Animated Stock Growth', artist='Matplotlib',comment='All stocks in portfolio')
    writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
    fig = plt.figure(dpi=200) 
    
    max_stock = stock_data[0][0][0]
    for s in range(0, len(stocks)):
        for val in stock_data[s]:
            if (val[0] > max_stock):
                max_stock = val[0]
    
    for stock in stocks:
        stock_names.append(stock)

    
    with writer.saving(fig, "animatedStockGrowth.mp4", dpi=200):
        for s in range(0, len(stocks)):
            nums = []
            for val in stock_data[s]:
                nums.append(val[0])
                #plt.clf()
                plt.ylim(0, max_stock+100)
                #plt.xlim(start_date.timestamp(), today.timestamp())
                #plt.xlim(737408.85, 737764.15)
                plt.xticks(rotation=45)
                plt.xlabel("Date")
                plt.ylabel("Price in USD")
                plt.title("Portfolio Growth")
                plt.plot(dates[0:len(nums)], nums, label=stock_names[s][0])
                plt.draw()
                plt.pause(0.05)
                writer.grab_frame()
            
    plt.show()

In [8]:
# Plots yields of stocks (and overall yield)
def plotStockYield(stocks, stock_data, duration):
    plt.figure(figsize=(15,5))
    plt.title("Stock Portfolio Yield - " + duration)
    plt.xlabel("Date")
    plt.ylabel("% Yield")
    
    today = datetime.today()
    #today = today.strftime("%Y/%m/%d")
    start_date = modifyDate(today, duration, len(stocks[0]))
    dates = pd.bdate_range(start=start_date,end=today)
    stock_names = []
    
    for stock in stocks:
        stock_names.append(stock)
        
    for s in range(0, len(stocks)):
        yield_percent = []
        starting_price = stock_data[s][0][0]
        for val in stock_data[s]:
            yield_percent.append(findYield(starting_price, val[0], 2))
        plt.plot(dates[0:len(yield_percent)], yield_percent, label=stock_names[s][0])

    plt.legend()
    plt.show()

In [9]:
# Plots overall portfolio growth
def plotPortfolioGrowth(stocks, stock_data, duration, total_amount_invested):
    plt.figure(figsize=(15,5))
    plt.title("Stock Portfolio Growth - " + duration)
    plt.xlabel("Date")
    plt.ylabel("Value in USD")
    
    today = datetime.today()
    #today = today.strftime("%Y/%m/%d")
    start_date = modifyDate(today, duration, len(stocks[0]))
    dates = pd.bdate_range(start=start_date,end=today)
    stock_names = []
    
    for stock in stocks:
        stock_names.append(stock)
        
    portfolio_val = []

    min_len_data = len(stock_data[0])
    for s in range(0, len(stocks)):
        if (len(stock_data[s]) < min_len_data):
            min_len_data = len(stock_data[s])
            
    stock_vals = np.zeros(min_len_data)
    
    for s in range(0, len(stocks)):
        nums = []
        amount_invested = total_amount_invested * stocks[s][1]
        num_shares = amount_invested / stock_data[s][0][0]
        
        for val in stock_data[s]:
            nums.append(val[0]*num_shares)
        stock_vals += nums[0:min_len_data]

    plt.plot(dates[0:len(stock_vals)], stock_vals)
    plt.show()
    

In [12]:
# FIELDS FOR USER TO ENTER

# Total amount invested
amount_invested = 10000 # User: Enter total amount to invest here

# Tuples with stock and allocation %
#stocks = [["AAPL", 0.3], ["MSFT", 0.1], ["AMZN", 0.2], ["TSLA", 0.3], ["GOOGL", 0.1]] # User: Enter tuples with a stock and it's percentage allocation as a decimal
stocks = [["AAPL", 0.25], ["MSFT", 0.25], ["XRX", 0.25], ["NLOK", 0.25]]
#stocks = [["VOO", 1]]

# Duration of Investment
duration_options = ["5d", "1mo", "3mo", "6mo", "1y", "2y", "5y", "10y", "ytd"]
duration = "ytd" # User: Pick which duration option you would like, and replace the value in the parenthesis with it

# Price Options - Determines whether stock is purchased/sold at open/close, high/low price of the day
price_options = ["open", "high", "low", "close"]
purchase_price = price_options.index("low") # User: Pick which price option you would like, and replace the value in the parenthesis with it
sell_price = price_options.index("high") # User: Pick which price option you would like, and replace the value in the parenthesis with it

stock_data = portfolioGenerator(stocks, amount_invested, purchase_price, sell_price, duration, 1, 2)
plotStockGrowth(stocks, stock_data, duration)
plotStockYield(stocks, stock_data, duration)
plotPortfolioGrowth(stocks, stock_data, duration, amount_invested)

AAPL  Starting: $ 2500.0  Ending: $ 4253.39   ytd  Yield:  70.14 %
MSFT  Starting: $ 2500.0  Ending: $ 3467.79   ytd  Yield:  38.71 %
XRX  Starting: $ 2500.0  Ending: $ 1619.58   ytd  Yield:  -35.22 %
NLOK  Starting: $ 2500.0  Ending: $ 3219.87   ytd  Yield:  28.79 %

Starting Portfolio Amount: $ 10000.0  Ending Portfolio Amount: $ 12560.63  Overall Yield:  25.61 %


In [14]:
animateStockGrowth(stocks, stock_data, duration)